In [1]:
import pandas as pd

In [2]:
import os
def load_universe():
    path_to_data = os.path.join(os.path.dirname("__file__"), './data/constituents.csv')
    return pd.read_csv(path_to_data)

In [3]:
df = load_universe()

In [4]:
df.head()

Symbol                 Name                  Sector
0    MMM           3M Company             Industrials
1    AOS      A.O. Smith Corp             Industrials
2    ABT  Abbott Laboratories             Health Care
3   ABBV          AbbVie Inc.             Health Care
4    ACN        Accenture plc  Information Technology

In [9]:
df['Symbol']

0        MMM
1        AOS
2        ABT
3       ABBV
4        ACN
5       ATVI
6        AYI
7       ADBE
8        AAP
9        AMD
10       AES
11       AET
12       AMG
13       AFL
14         A
15       APD
16      AKAM
17       ALK
18       ALB
19       ARE
20      ALXN
21      ALGN
22      ALLE
23       AGN
24       ADS
25       LNT
26       ALL
27     GOOGL
28      GOOG
29        MO
       ...  
475     VRTX
476     VIAB
477        V
478      VNO
479      VMC
480      WMT
481      WBA
482       WM
483      WAT
484      WEC
485      WFC
486     WELL
487      WDC
488       WU
489      WRK
490       WY
491      WHR
492      WMB
493     WLTW
494      WYN
495     WYNN
496      XEL
497      XRX
498     XLNX
499       XL
500      XYL
501      YUM
502      ZBH
503     ZION
504      ZTS
Name: Symbol, Length: 505, dtype: object

In [5]:
df.head()

Symbol                 Name                  Sector
0    MMM           3M Company             Industrials
1    AOS      A.O. Smith Corp             Industrials
2    ABT  Abbott Laboratories             Health Care
3   ABBV          AbbVie Inc.             Health Care
4    ACN        Accenture plc  Information Technology

In [6]:
import alpaca_trade_api as tradeapi
import pandas as pd
import os
import logging
from logging.config import fileConfig
from datetime import timedelta, datetime
import time
import concurrent
import requests

fileConfig("./logging_config.ini")
logger = logging.getLogger("__file__")

TOMORROW = datetime.now() + timedelta(days=1)

os.environ["APCA_API_KEY_ID"] = "AK369OPHSF98F2J623N7"
os.environ["APCA_API_SECRET_KEY"] = "ajb8sATuQQjJUwKMcVK829o4j5UAidin4spC7t/9"

NY = "America/New_York"

class Algo:

    def __init__(self, done=TOMORROW):
        logger.info("instantiating class")
        self.universe = self.load_universe()
        self.done = done
        self.api = tradeapi.REST(base_url="https://paper-api.alpaca.markets")


    def load_universe(self):
        logger.info("loading universe")
        path_to_data = os.path.join(os.path.dirname("__file__"), './data/constituents.csv')
        return pd.read_csv(path_to_data)

    def prices(self, symbols):
        """
        get prices from list of symbols
        """
        logger.info("getting prices")
        now = pd.Timestamp.now(tz=NY)
        end_dt = now

        if end_dt.time() >= pd.Timestamp("09:30", tz=NY).time():
            end_dt = now - pd.Timedelta(now.strftime("%H:%M:%S")) - pd.Timedelta("1 minute")
        return self._get_iex_prices(symbols, end_dt)

    def __get_iex_barset_prices(self, symbols, from_date, to_date, limit=50, interval="day"):
        logging.info("calling alpaca barset to get iex stats on symbols {} from {} to {}".format(str(symbols), str(from_date), str(to_date)))
        r = requests.get("https://data.alpaca.markets/v1/bars/{}".format(interval), \
            params={"symbols": ",".join(symbols), "limit": limit, "start": from_date, "end": to_date}, \
            headers={"APCA_API_KEY_ID": os.environ["APCA_API_KEY_ID"], "APCA_API_SECRET_KEY": os.environ["APCA_API_SECRET_KEY"]})
        logger.info("request made to: {}".format(r.url))
        logger.info("request returned with status of {}".format(str(r.status_code)))
        return r.json()

    def _get_iex_prices(self, symbols, end_dt):
        logger.info("calling alpaca data api to get iex stats on {} symbols for 50 days".format(str(len(symbols))))

        from_date = (end_dt - pd.Timedelta("50 days")).strftime("%Y-%m-%d")
        to_date = end_dt.strftime("%Y-%m-%d")

        # queries 200 of them at the same time
        logger.info("requesting for the first 200 symbols")
        barset = self.__get_iex_barset_prices(symbols[0:200], from_date=from_date, to_date=to_date)
        for x in range(200, len(symbols), 200):
            logger.info("requesting for the next {} symbols".format(str(x)))
            barset.update(self.__get_iex_barset_prices(symbols[x:x+200], from_date=from_date, to_date=to_date))
        return barset

    def main(self):
        while True:

            clock = self.api.get_clock()
            now = clock.timestamp

            if clock.is_open and done != now.strftime("%Y-%m-%d"):

                # execute some trades
                done = now.strftime("%Y-%m-%d")
                logger.info("finished executing tick at {}".format(done))

            time.sleep(1)
            
a = Algo()
sp500_symbols = a.universe["Symbol"].tolist()
prices = a.prices(sp500_symbols)


2019-01-04 01:07:13,228 - __file__ - INFO - instantiating class
2019-01-04 01:07:13,231 - __file__ - INFO - loading universe
2019-01-04 01:07:13,260 - __file__ - INFO - getting prices
2019-01-04 01:07:14,086 - __file__ - INFO - calling alpaca data api to get iex stats on 505 symbols for 50 days
2019-01-04 01:07:14,094 - __file__ - INFO - requesting for the first 200 symbols
2019-01-04 01:07:14,095 - root - INFO - calling alpaca barset to get iex stats on symbols ['MMM', 'AOS', 'ABT', 'ABBV', 'ACN', 'ATVI', 'AYI', 'ADBE', 'AAP', 'AMD', 'AES', 'AET', 'AMG', 'AFL', 'A', 'APD', 'AKAM', 'ALK', 'ALB', 'ARE', 'ALXN', 'ALGN', 'ALLE', 'AGN', 'ADS', 'LNT', 'ALL', 'GOOGL', 'GOOG', 'MO', 'AMZN', 'AEE', 'AAL', 'AEP', 'AXP', 'AIG', 'AMT', 'AWK', 'AMP', 'ABC', 'AME', 'AMGN', 'APH', 'APC', 'ADI', 'ANDV', 'ANSS', 'ANTM', 'AON', 'APA', 'AIV', 'AAPL', 'AMAT', 'APTV', 'ADM', 'ARNC', 'AJG', 'AIZ', 'T', 'ADSK', 'ADP', 'AZO', 'AVB', 'AVY', 'BHGE', 'BLL', 'BAC', 'BAX', 'BBT', 'BDX', 'BRK.B', 'BBY', 'BIIB', 'B

2019-01-04 01:07:15,411 - __file__ - INFO - request returned with status of 200


In [5]:
a = Algo()

NameError: name 'Algo' is not defined

In [10]:
sp500_symbols = a.universe["Symbol"].tolist()

In [11]:
prices_df = a.prices(sp500_symbols)

2018-12-30 22:31:26,519 - root - INFO - calling alpaca barset to get iex stats on symbols ['MMM', 'AOS', 'ABT', 'ABBV', 'ACN', 'ATVI', 'AYI', 'ADBE', 'AAP', 'AMD', 'AES', 'AET', 'AMG', 'AFL', 'A', 'APD', 'AKAM', 'ALK', 'ALB', 'ARE', 'ALXN', 'ALGN', 'ALLE', 'AGN', 'ADS', 'LNT', 'ALL', 'GOOGL', 'GOOG', 'MO', 'AMZN', 'AEE', 'AAL', 'AEP', 'AXP', 'AIG', 'AMT', 'AWK', 'AMP', 'ABC', 'AME', 'AMGN', 'APH', 'APC', 'ADI', 'ANDV', 'ANSS', 'ANTM', 'AON', 'APA', 'AIV', 'AAPL', 'AMAT', 'APTV', 'ADM', 'ARNC', 'AJG', 'AIZ', 'T', 'ADSK', 'ADP', 'AZO', 'AVB', 'AVY', 'BHGE', 'BLL', 'BAC', 'BAX', 'BBT', 'BDX', 'BRK.B', 'BBY', 'BIIB', 'BLK', 'HRB', 'BA', 'BKNG', 'BWA', 'BXP', 'BSX', 'BHF', 'BMY', 'AVGO', 'BF.B', 'CHRW', 'CA', 'COG', 'CDNS', 'CPB', 'COF', 'CAH', 'KMX', 'CCL', 'CAT', 'CBOE', 'CBRE', 'CBS', 'CELG', 'CNC', 'CNP', 'CTL', 'CERN', 'CF', 'SCHW', 'CHTR', 'CVX', 'CMG', 'CB', 'CHD', 'CI', 'XEC', 'CINF', 'CTAS', 'CSCO', 'C', 'CFG', 'CTXS', 'CME', 'CMS', 'KO', 'CTSH', 'CL', 'CMCSA', 'CMA', 'CAG', 'CXO',

ValueError: arrays must all be same length

In [14]:
prices

{'A': [{'t': 1539748800,
   'o': 67.17,
   'h': 67.46,
   'l': 66.31,
   'c': 67.2,
   'v': 1991212},
  {'t': 1539835200,
   'o': 67.12,
   'h': 67.2,
   'l': 65.255,
   'c': 65.75,
   'v': 2327330},
  {'t': 1539921600,
   'o': 65.81,
   'h': 66.24,
   'l': 64.24,
   'c': 64.47,
   'v': 2418302},
  {'t': 1540180800,
   'o': 64.69,
   'h': 64.84,
   'l': 63.54,
   'c': 64.28,
   'v': 2227932},
  {'t': 1540267200,
   'o': 62.82,
   'h': 63.13,
   'l': 61.38,
   'c': 62.73,
   'v': 4219761},
  {'t': 1540353600,
   'o': 62.92,
   'h': 63.76,
   'l': 61.01,
   'c': 61.13,
   'v': 3481246},
  {'t': 1540440000,
   'o': 61.49,
   'h': 62.89,
   'l': 61.07,
   'c': 62.61,
   'v': 3318277},
  {'t': 1540526400,
   'o': 61.82,
   'h': 63.11,
   'l': 61.13,
   'c': 62.73,
   'v': 3119947},
  {'t': 1540785600,
   'o': 63.65,
   'h': 64.17,
   'l': 61.13,
   'c': 62.08,
   'v': 2919874},
  {'t': 1540872000,
   'o': 62.35,
   'h': 63.72,
   'l': 61.68,
   'c': 63.64,
   'v': 3076720},
  {'t': 15409584

In [15]:
prices_df = pd.Series(prices).apply(lambda x  : pd.Series({ k: v for y in x for k, v in y.items() }))

In [16]:
prices_df.head()

t       o       h         l       c           v
A     1.545973e+09   66.98   67.12   65.7100   65.96   1927748.0
AAL   1.545973e+09   32.17   32.60   31.5100   31.83   6375395.0
AAP   1.545973e+09  155.34  157.30  153.6395  155.46   1009498.0
AAPL  1.545973e+09  157.50  158.52  154.5500  156.23  41740084.0
ABBV  1.545973e+09   90.09   92.82   90.0000   91.12   6037743.0

In [ ]:
prices_df

In [2]:
pd

NameError: name 'pd' is not defined

In [3]:
prices_df.head()

NameError: name 'prices_df' is not defined

In [4]:
import pandas as pd

In [22]:
data = {'ticker': [], 't': [], 'o': [], 'h': [], 'l': [], 'c': [], 'v': []}
for k, v in prices.items():
    for entry in v:
        data['ticker'].append(k)
    for name in ['t', 'o', 'h', 'l', 'c', 'v']:
        for entry in v:
            data[name].append(entry.get(name))
prices_df = pd.DataFrame(data)

In [ ]:
p

In [24]:
prices_df.head(n=51)

ticker           t        o        h        l        c        v
0       A  1540180800  64.6900  64.8400  63.5400  64.2800  2227932
1       A  1540267200  62.8200  63.1300  61.3800  62.7300  4219761
2       A  1540353600  62.9200  63.7600  61.0100  61.1300  3481246
3       A  1540440000  61.4900  62.8900  61.0700  62.6100  3318277
4       A  1540526400  61.8200  63.1100  61.1300  62.7300  3119947
5       A  1540785600  63.6500  64.1700  61.1300  62.0800  2919874
6       A  1540872000  62.3500  63.7200  61.6800  63.6400  3076720
7       A  1540958400  64.3500  65.9800  64.1900  64.7900  3820987
8       A  1541044800  65.0700  65.3400  64.5850  65.2200  1882438
9       A  1541131200  65.8000  66.6100  65.4350  65.9300  2272114
10      A  1541394000  66.0300  66.3900  65.2300  65.9100  2348704
11      A  1541480400  66.0400  66.4200  65.6700  65.9800  2287255
12      A  1541566800  66.5100  68.3800  66.2750  68.2600  2700613
13      A  1541653200  67.9900  68.3600  67.3800  67.7900  2444607
14      A  1541739600  67.6000  67.7600  66.7000  67.2700  2573534
15      A  1541998800  66.1600  66.2500  64.4500  64.5000  2999960
16      A  1542085200  64.5900  65.4700  63.9400  64.3400  2216456
17      A  1542171600  64.6400  64.8400  63.2800  63.4700  4852556
18      A  1542258000  63.3200  64.9500  62.5400  64.7200  3846090
19      A  1542344400  64.3800  65.6000  64.3800  64.9900  2963305
20      A  1542603600  64.6700  64.9600  62.4000  62.6100  3392057
21      A  1542690000  66.2500  68.4324  64.9300  67.5200  8187326
22      A  1542776400  67.6600  68.6700  67.1900  67.7200  3557551
23      A  1542949200  67.0400  68.6100  67.0400  68.2100  1374274
24      A  1543208400  68.9400  69.3000  68.3900  69.2500  2406265
25      A  1543294800  68.8700  69.5200  68.7000  69.3600  2533581
26      A  1543381200  69.8200  71.4850  69.4300  71.4800  2661339
27      A  1543467600  71.2300  72.1800  71.2300  71.5700  2625819
28      A  1543554000  71.6300  72.6450  71.3400  72.3500  2279473
29      A  1543813200  73.3300  74.7900  73.1900  74.6700  4265221
30      A  1543899600  74.7000  75.1150  72.6300  72.9100  4263802
31      A  1544072400  71.2000  71.9300  69.9000  71.9100  3505914
32      A  1544158800  71.7100  72.0900  69.6500  70.2500  2184502
33      A  1544418000  70.4300  70.7100  68.5700  70.5900  2347157
34      A  1544504400  71.7600  72.4400  70.7000  71.0500  2926016
35      A  1544590800  72.1700  73.0400  71.6000  71.7500  2842861
36      A  1544677200  72.1400  72.6800  70.9000  71.1400  2200718
37      A  1544763600  70.4200  70.6100  69.1300  69.3600  1982726
38      A  1545022800  69.1100  69.6250  67.4000  67.8500  2241705
39      A  1545109200  68.4500  69.0300  67.3900  67.9900  2111981
40      A  1545195600  68.2700  69.0900  65.8100  66.8300  2845468
41      A  1545282000  66.3300  66.4600  64.5900  65.1900  3547814
42      A  1545368400  65.2200  66.2300  63.2200  63.2900  4683100
43      A  1545627600  62.9300  63.6300  62.2200  62.6700  1668490
44      A  1545800400  62.9300  65.5800  62.7600  65.5400  1701769
45      A  1545886800  64.5000  66.5000  64.0000  66.4800  1655033
46      A  1545973200  66.9800  67.1200  65.7100  65.9600  1927748
47      A  1546232400  66.3400  67.4800  66.3400  67.4600  1571616
48      A  1546405200  66.5000  66.5700  65.3000  65.6900  2078511
49      A  1546491600  65.5300  65.7800  62.0000  63.2700  5383926
50    AAL  1540180800  32.1812  32.4305  31.7324  32.0715  7572134

In [17]:
prices_df[0][1]

[{'t': 1540180800,
  'o': 32.1812,
  'h': 32.4305,
  'l': 31.7324,
  'c': 32.0715,
  'v': 7572134},
 {'t': 1540267200,
  'o': 31.4432,
  'h': 32.3507,
  'l': 30.5158,
  'c': 32.2909,
  'v': 12468259},
 {'t': 1540353600,
  'o': 32.3906,
  'h': 32.6598,
  'l': 30.1567,
  'c': 30.2565,
  'v': 15348177},
 {'t': 1540440000,
  'o': 31.1041,
  'h': 33.2382,
  'l': 31.0343,
  'c': 32.2809,
  'v': 18375181},
 {'t': 1540526400,
  'o': 31.3136,
  'h': 32.9191,
  'l': 31.2138,
  'c': 32.3706,
  'v': 11438628},
 {'t': 1540785600,
  'o': 33.0488,
  'h': 33.9014,
  'l': 31.862,
  'c': 32.5103,
  'v': 9405453},
 {'t': 1540872000,
  'o': 32.3507,
  'h': 34.6843,
  'l': 32.241,
  'c': 34.5646,
  'v': 13067628},
 {'t': 1540958400,
  'o': 35.0632,
  'h': 35.8012,
  'l': 34.7142,
  'c': 34.9834,
  'v': 11132795},
 {'t': 1541044800,
  'o': 35.2028,
  'h': 36.3696,
  'l': 34.9735,
  'c': 36.2699,
  'v': 9643154},
 {'t': 1541131200,
  'o': 36.4893,
  'h': 37.3569,
  'l': 35.5419,
  'c': 36.23,
  'v': 10039121

In [8]:
prices_df.head()

A       [{'t': 1540180800, 'o': 64.69, 'h': 64.84, 'l'...
AAL     [{'t': 1540180800, 'o': 32.1812, 'h': 32.4305,...
AAP     [{'t': 1540180800, 'o': 164.3269, 'h': 165.586...
AAPL    [{'t': 1540180800, 'o': 219.0258, 'h': 222.583...
ABBV    [{'t': 1540180800, 'o': 88.53, 'h': 88.53, 'l'...
dtype: object

In [9]:
prices_df.T.head()

A       [{'t': 1540180800, 'o': 64.69, 'h': 64.84, 'l'...
AAL     [{'t': 1540180800, 'o': 32.1812, 'h': 32.4305,...
AAP     [{'t': 1540180800, 'o': 164.3269, 'h': 165.586...
AAPL    [{'t': 1540180800, 'o': 219.0258, 'h': 222.583...
ABBV    [{'t': 1540180800, 'o': 88.53, 'h': 88.53, 'l'...
dtype: object

In [11]:
prices_df = pd.DataFrame(prices)

ValueError: arrays must all be same length